# TP d'analyse numérique n°6

Dans ce TP, on s'intéresse aux méthodes numériques de résolution des équations différentielles.

### Exercice 1

À titre d'exemple, nous allons manipuler une équation différentielle vectorielle (en dimension 2), déterminant la chute d'une pierre subissant des frottements fluides. On se place dans le plan vertical contenant la vitesse et le point de départ, et la solution est donc une courbe paramétrée $X: \mathbb{R} \to \mathbb{R}^2$ envoyant le temps $t$ sur le vecteur position $X(t)$ dont les deux coordonnées sont l'horizontale et la verticale du point. 
Selon la théorie de Newton, on a la force totale appliquée
$$F = mg \pmatrix{0 \\ -1}  -c ||X'||X'$$
où $mg$ correspond à la gravité et $-c ||X'|| X'=-c \frac{X'}{||X'||} ||X'||^2$ aux frottements fluides,  de norme proportionnelle au carré de la vitesse et orientés dans le sens inverse de celle-ci.
L'équation différentielle régissant $X$ est alors donnée par la loi de Newton $F = m X''$, soit
$$X''=g\pmatrix{0 \\ -1} - \frac{c}{m} ||X'|| X'$$
qu'on ramène à une équation vectorielle d'ordre 1 en posant $Y=\pmatrix{X \\ X'}$ (donc dans $\mathbb{R}^4$). On obtient ainsi
$$Y'(t)=f(t,Y)$$
où $f$ est la fonction envoyant 
$$Y=\pmatrix{y_0 \\ y_1 \\ y_2 \\ y_3} \mapsto \pmatrix{y_2 \\ y_3 \\ -\frac{c}{m}\sqrt{y_2^2+y_3^2} y_2 \\ -g - \frac{c}{m}\sqrt{y_2^2+y_3^2}y_3}$$

On commence donc par définir cette fonction $f$ (qui se trouve être indépendante de $t$). Les paramètres $g$, $m$ et $c$ sont stockés dans `params` et il faudra les donner pour toute résolution.

In [ ]:
def f(t,Y,params):
     return [Y[2],
            Y[3],
           -params[2]/params[1]*sqrt(Y[2]^2+Y[3]^2)*Y[2],
           -params[0]-params[2]/params[1]*sqrt(Y[2]^2+Y[3]^2)*Y[3]]

On définit ensuite un *solver* d'équations différentielles (un objet dont les méthodes effectuent la résolution) et on lui attache la fonction comme attribut `function`.

In [ ]:
U=ode_solver()
U.function=f

On lui demande d'effectuer la résolution numérique en donnant la condition initiale, l'intervalle de temps, le nombre de points d'approximation, et la valeur des paramètres.
Ici, nous demandons donc que la pierre soit lancée à partir du point $(0,0)$, avec une vitesse horizontale de $5\ m.s^{1}$ et verticale de $10\ m.s^{-1}$, nous voulons la trajectoire pendant 2 secondes, avec une gravité de $9.81\ m.s^{-2}$, une masse de $10 kg$ et coefficient de frottements fluides nulle (dans toutes ces unités, $m$ est bien entendu le mêtre, pas la masse précédente). C'est donc ce qui se passerait si la terre n'avait pas d'athmosphère, dans le vide.

In [ ]:
U.ode_solve(y_0=[0,0,5,10],
            t_span=[0,2],
            params=[9.81,10,0],
            num_points=100)

À partir de maintenant, la solution approchée est stockée dans la variable U.solution. C'est en fait juste une liste de valeurs approchées de la solution, pour chaque valeur de $t$ dans la subdivision de `t_span` en `num_points` points.

On peut demander de fabriquer des fonctions interpolées à partir de ces listes de valeurs, pour pouvoir ensuite demander la valeur de la solution approchée en tout point (pas seulement aux points de la subdivision).

In [ ]:
u=U.interpolate_solution()
v=U.interpolate_solution(i=1)

On crée une séquence de paires avec les deux coordonnées d'une solution, pour pouvoir la tracer.

In [ ]:
seq=[(u(0.1*i),v(0.1*i)) for i in range(200)]

On crée un objet graphique "mondessin" et on lui rajoute le traçage (plot) des points donnés, en les joignant.

In [ ]:
mondessin=Graphics()
mondessin+=list_plot(seq,plotjoined=True)

On en demande l'affichage.

In [ ]:
mondessin.show(aspect_ratio=1)

On recommence, cette fois avec des frottements de $1\ kg.m^{-1}$.

In [ ]:
U.ode_solve(y_0=[0,0,5,10],
            t_span=[0,2],
            params=[9.81,10,1],
            num_points=100)

In [ ]:
u=U.interpolate_solution()
v=U.interpolate_solution(i=1)
seq=[(u(0.1*i),v(0.1*i)) for i in range(200)]

On rajoute au même objet graphique la nouvelle courbe, pour voir la différence entre la situation sans frottements et avec frottements.

In [ ]:
mondessin+=list_plot(seq,plotjoined=True)
mondessin.show(aspect_ratio=1)

In [ ]:
U.ode_solve(y_0=[0,0,5,10],
            t_span=[0,4],
            params=[9.81,10,1],
            num_points=200)

In [ ]:
u=U.interpolate_solution()
v=U.interpolate_solution(i=1)
seq=[(u(0.1*i),v(0.1*i)) for i in range(400)]

In [ ]:
mondessin+=list_plot(seq,plotjoined=True)
mondessin.show(aspect_ratio=1)

### Exercice 2

On considère les équations de Lotka-Volterra d'un système proie-prédateurs. Les paramètres sont les constantes (a priori positives) qui déterminent le taux de mortalité etc. de chaque espèce.

$$\left\{
\begin{array}{l}
x'(t) = a\,x(t)-b\,x(t)y(t) \\
y'(t) = -c\,y(t)+d\,x(t)y(t)
\end{array}\right.$$

Le nombre de proies est $x$, le nombre de prédateurs $y$, et

 - le taux de natalité moins mortalité naturel en l'absence de prédateurs des proies est $a$
 - le taux de mortalité des proies dû aux prédateurs est $b$
 - le taux de mortalité des prédateurs (en l'abscence de proies) est $c$
 - le taux de natalité des prédateurs grâce aux proies mangées est $d$

In [ ]:
def f(t,y,params):
     return[params[0]*y[0]-params[1]*y[0]*y[1],
            -params[2]*y[1]+params[3]*y[0]*y[1]]

In [ ]:
T=ode_solver()
T.function=f

In [ ]:
T.ode_solve(y_0=[1,1],
            t_span=[0,100],
            params=[0.66,1.33,1,1],
            num_points=1000)

In [ ]:
u=T.interpolate_solution()
v=T.interpolate_solution(i=1)
seq=[(u(0.1*i),v(0.1*i)) for i in range(1000)]

In [ ]:
mongraphe=Graphics()
mongraphe+=list_plot(seq,plotjoined=True)

In [ ]:
mongraphe.show()

In [ ]:
mongraphe=Graphics()
for i in range(20):
    T.ode_solve(y_0=[1,1+0.05*i],
            t_span=[0,100],
            params=[0.66,1.33,1,1],
            num_points=1000)
    u=T.interpolate_solution()
    v=T.interpolate_solution(i=1)
    seq=[(u(0.1*j),v(0.1*j)) for j in range(1000)]
    mongraphe+=list_plot(seq,plotjoined=True)
    mongraphe+=circle((1,1+0.05*i),0.02,rgbcolor=(1,0,0))
mongraphe.show()

### Exercice 3

Dans l'exercice 1, nous n'avons pas précisé au solveur la méthode de résolution numérique qu'il devait utiliser. Dans cet exercice, nous allons en utiliser plusieurs différentes et les comparer.

Pour cela, utilisons une équation différentielle dont nous connaissons bien les solution: $y''(t)=-y(t)$, qui a pour base de solutions $\sin$ et $\cos$.

In [ ]:
def g(t,y):
    return [y[1],-y[0]]

In [ ]:
U=ode_solver()
U.function=g

In [ ]:
U.algorithm="rk4"

In [ ]:
U.ode_solve(y_0=[0,1],
            t_span=[0,32],
            num_points=20)

In [ ]:
u=U.interpolate_solution()

In [ ]:
mongraphe=Graphics()

In [ ]:
mongraphe+=plot(u,xmin=0,xmax=32)

In [ ]:
mongraphe+=plot(sin,xmin=0,xmax=32,color='red')

In [ ]:
show(mongraphe)

In [ ]:
t, x, y = PolynomialRing(RR,3,"txy").gens()
f = y; g = -x

In [ ]:
from sage.calculus.desolvers import eulers_method_2x2
mylist = eulers_method_2x2(f,g, 0, 0, 1, 0.01, 32,algorithm="none")

In [ ]:
pts=[[s[0],s[1]] for s in mylist]

In [ ]:
P1 = list_plot(pts)
P2 = line(pts)
(P1+P2).show()